In [12]:
from typing import Dict, Optional, Any
import numpy as np
import gym
#from gym import spaces
import torch
from gymnasium import spaces
class CustomEnv(gym.Env):
    def __init__(self, S, A, R):
        self.S = S #torch.tensor(S, dtype=torch.float32)  # Convert S to torch tensor
        self.A = A#torch.tensor(A, dtype=torch.float32)  # Convert A to torch tensor
        self.R = R  if R is not None else None #torch.tensor(R, dtype=torch.float32)  # Convert R to torch tensor if provided
        self.num_samples = self.S.shape[0]
        self.current_step = 0
        
        # Action space: assume discrete actions for simplicity
        self.action_dim = self.A.shape[1]
        self.observation_dim = self.S.shape[1]
        self.action_space = spaces.box.Box(low=-1e6, high=1e6, shape=(self.action_dim,))
        
        # Observation space: separate S and Y with specific labels
        # obs_dim_S = self.S.shape[1]
        # observation_space = {}
        # for i in range(obs_dim_S):
        #     observation_space[f'S_{i+1}'] = spaces.Box(low=-np.inf, high=np.inf, shape=(1,), dtype=np.float32)
        
        self.observation_space = spaces.box.Box(low=-np.inf, high=np.inf, shape=(self.observation_dim,))
        


    def reset(self, seed: int = None, options: Optional[Dict[str, Any]] = None):
        super().reset(seed=seed, options=options)
        #self.state = self.observation_space.sample()

        # self.current_step = 0  # Reset current step
        self.current_step = np.random.randint(0, self.S.shape[0])
        self.state = self.S[self.current_step,:]
        return self.state, {}
    


    def step(self,action): # action
        #print(self.state)
        #print(action)
        action = torch.from_numpy(action.astype(np.float64) )
        #reward = -np.abs(self.state.mean() - action.mean()) # 先假設這樣寫，這邊要REWIEW
        #self.state = self.observation_space.sample()
        #print(action.shape)
        
        

        reward = torch.mean(self.A[self.current_step,:] - action)**(-1)
        #reward = None
        print(self.current_step)
        
        self.state = self.S[self.current_step,:]
        #done = (self.current_step == self.obs_dim_S - 1)
        #print("done",done)
        # self.current_step = self.current_step + 1
        self.current_step = (self.current_step + 1) % self.S.shape[0]
        done = (self.current_step == self.num_samples - 1)
        # observation, reward, terminated, truncated, info
        return self.state, reward, done, False, {}
    

    
    #### 
    # def step(self, action):
    #     # Apply action and get next state and reward
    #     #next_state = self._get_observation()
    #     self.state = self.observation_space.sample()
    #     reward = self._calculate_reward(action)
    #     #done = (self.current_step == self.num_samples - 1)
    #     #self.current_step = (self.current_step + 1) % self.num_samples
    #     return self.state, reward, False, False, {}
    
    # def _get_observation(self):
    #     obs = {}
    #     for i in range(self.S.shape[1]):
    #         obs[f'S_{i+1}'] = np.array([self.S[self.current_step, i]])
    #     return obs
    
    # def _calculate_reward(self, action):
    #     # Example: using a reward matrix R based on expected Y values
    #     if self.R is not None:
    #         ideal_y = self.R[action]  # Ideal Y value for the chosen action
    #         actual_y = self.S[self.current_step]  # Actual Y value
    #         reward = -torch.norm(actual_y - ideal_y)  # Negative L2 norm difference as reward
    #     else:
    #         # Default reward function (replace with your own logic)
    #         reward = torch.sum(self.A[self.current_step] * action)
        
    #     return reward

In [13]:
from gymnasium.wrappers import TimeLimit
from imitation.data import rollout
from imitation.data.wrappers import RolloutInfoWrapper
from stable_baselines3.common.vec_env import DummyVecEnv,SubprocVecEnv
import numpy as np

# 假設 S 和 A 是你的狀態和動作矩陣
S = np.random.rand(1000, 9)
A = np.random.rand(10000, 45)

S = torch.from_numpy(S)
A = torch.from_numpy(A)
#env = CustomEnv(S, A,R=None)

#env = TimeLimit(env, max_episode_steps=500)

# Create a vectorized environment for training with `imitation`


# Option A: use a helper function to create multiple environments
def _make_env(s=S,a=A,R=None):
    """Helper function to create a single environment. Put any logic here, but make sure to return a RolloutInfoWrapper."""
    _env = CustomEnv(s,a,R)
    _env = TimeLimit(_env, max_episode_steps=500)
    _env = RolloutInfoWrapper(_env)
    return _env

In [14]:
# venv = DummyVecEnv([_make_env for _ in range(4)])
venv = DummyVecEnv([_make_env for _ in range(1)])
#venv = SubprocVecEnv([_make_env for _ in range(4)])
#vec_env = DummyVecEnv([lambda: env])

In [15]:
from imitation.rewards.reward_nets import BasicShapedRewardNet
from imitation.util.networks import RunningNorm
reward_net = BasicShapedRewardNet(
    observation_space=venv.observation_space,
    action_space=venv.action_space,
    normalize_input_layer=RunningNorm,
)

In [16]:
SEED = np.random.randint(0, S.shape[0])

In [7]:
from stable_baselines3 import PPO
from stable_baselines3.ppo import MlpPolicy
from stable_baselines3.common.evaluation import evaluate_policy
from gymnasium.wrappers import TimeLimit

expert = PPO(
    policy=MlpPolicy,
    env=venv,
    seed=SEED, #下SEED會影響到INDEX抽樣# np.random.randint(0, self.S.shape[0])
    batch_size=64,
    ent_coef=0.0,
    learning_rate=0.0003,
    n_epochs=10,
    n_steps=64,
)

In [8]:
reward, _ = evaluate_policy(expert, venv, 100)
print(f"Reward before training: {reward}")

c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\stable_baselines3\common\evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\imitation\data\types.py:279: UserWarning: tried to wrap <class 'torch.Tensor'> as an observation
  warnings.warn(f"tried to wrap {type(obs)} as an observation")


510
511
512
513
514
515
516
517
518
519
520
521
522
523
524
525
526
527
528
529
530
531
532
533
534
535
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
565
566
567
568
569
570
571
572
573
574
575
576
577
578
579
580
581
582
583
584
585
586
587
588
589
590
591
592
593
594
595
596
597
598
599
600
601
602
603
604
605
606
607
608
609
610
611
612
613
614
615
616
617
618
619
620
621
622
623
624
625
626
627
628
629
630
631
632
633
634
635
636
637
638
639
640
641
642
643
644
645
646
647
648
649
650
651
652
653
654
655
656
657
658
659
660
661
662
663
664
665
666
667
668
669
670
671
672
673
674
675
676
677
678
679
680
681
682
683
684
685
686
687
688
689
690
691
692
693
694
695
696
697
698
699
700
701
702
703
704
705
706
707
708
709
710
711
712
713
714
715
716
717
718
719
720
721
722
723
724
725
726
727
728
729
730
731
732
733
734
735
736
737
738
739
740
741
742
743
744
745
746
747
748
749
750
751
752
753
754
755
756
757
758
759


In [85]:
new_obs = np.random.randn(1,S.shape[1])
new_obs = torch.from_numpy(new_obs)


In [86]:
expert.predict(new_obs,deterministic=True)

(array([[ 7.0690275e-03,  4.2365221e-03,  1.4112808e-03,  2.1671155e-04,
          4.1989386e-03, -2.6323898e-03, -2.7270610e-03, -3.0386471e-04,
          4.0554376e-03, -6.5475004e-05, -9.8537449e-03, -1.2377836e-02,
         -3.7882212e-03, -4.3931967e-03,  3.3039157e-03, -3.6583690e-03,
          1.3936916e-03, -1.9271544e-03, -2.4522038e-03,  2.4866778e-05,
          8.0802878e-03,  7.2866264e-03,  5.8695734e-03,  8.7754102e-05,
         -4.4118492e-03, -6.2090955e-03,  4.3759979e-03, -1.0209391e-03,
         -3.6376871e-03,  2.1305224e-03,  4.5805052e-04,  4.6481672e-03,
         -3.7358142e-03,  5.4718833e-03,  8.7271556e-03,  3.7355721e-04,
         -7.0581608e-04,  1.3766228e-02, -3.1261009e-03, -1.8364913e-03,
          1.9479657e-03, -4.4766250e-03,  2.0897668e-03, -5.6361645e-03,
          3.1894895e-03]], dtype=float32),
 None)

In [91]:
rrrrr.step

<bound method VecEnv.step of <stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv object at 0x000001E35A66AA00>>

In [9]:
rng = np.random.default_rng(seed=SEED)
rollouts = rollout.rollout(
    expert,
    venv,
    rollout.make_sample_until(min_timesteps=None, min_episodes=50),
    rng=rng
    )
transitions = rollout.flatten_trajectories(rollouts)



465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
490
491
492
493
494
495
496
497
498
499
500
501
502
503
504
505
506
507
508
509
510
511
512
513
514
515
516
517
518
519
520
521
522
523
524
525
526
527
528
529
530
531
532
533
534
535
536
537
538
539
540
541
542
543
544
545
546
547
548
549
550
551
552
553
554
555
556
557
558
559
560
561
562
563
564
565
566
567
568
569
570
571
572
573
574
575
576
577
578
579
580
581
582
583
584
585
586
587
588
589
590
591
592
593
594
595
596
597
598
599
600
601
602
603
604
605
606
607
608
609
610
611
612
613
614
615
616
617
618
619
620
621
622
623
624
625
626
627
628
629
630
631
632
633
634
635
636
637
638
639
640
641
642
643
644
645
646
647
648
649
650
651
652
653
654
655
656
657
658
659
660
661
662
663
664
665
666
667
668
669
670
671
672
673
674
675
676
677
678
679
680
681
682
683
684
685
686
687
688
689
690
691
692
693
694
695
696
697
698
699
700
701
702
703
704
705
706
707
708
709
710
711
712
713
714


In [10]:
from imitation.algorithms.adversarial.airl import AIRL
airl_trainer = AIRL(
    demonstrations=rollouts,
    demo_batch_size=2048,
    gen_replay_buffer_capacity=512,
    n_disc_updates_per_round=16,
    venv=venv,
    gen_algo=expert,
    reward_net=reward_net,
)


In [11]:
venv.seed(SEED)
learner_rewards_before_training, _ = evaluate_policy(
    expert, venv, 100, return_episode_rewards=True,
)


271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
353
354
355
356
357
358
359
360
361
362
363
364
365
366
367
368
369
370
371
372
373
374
375
376
377
378
379
380
381
382
383
384
385
386
387
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
490
491
492
493
494
495
496
497
498
499
500
501
502
503
504
505
506
507
508
509
510
511
512
513
514
515
516
517
518
519
520


In [65]:
print(np.mean(learner_rewards_before_training))
expert.predict(new_obs,deterministic=True)

973.2981192493439


(array([[-4.9704066e-03, -2.9512034e-03, -3.8709978e-03, -1.5201775e-03,
         -3.7438609e-03,  4.1609872e-03,  2.7136467e-03,  4.6425788e-03,
         -6.8412279e-04,  2.6093577e-03, -3.4552373e-03, -4.4772876e-03,
          5.4676719e-03,  9.6433796e-03, -1.7450592e-03,  4.1021314e-04,
         -4.9753762e-03,  6.6392496e-04, -9.2622321e-03, -2.6082529e-03,
         -5.8745621e-03, -6.6485684e-03,  9.4102155e-03, -7.9215532e-03,
         -2.0311750e-03, -4.1278689e-03, -1.2732111e-05, -2.9133167e-04,
         -1.1158218e-02,  4.9406518e-03, -1.4419546e-03, -1.3260334e-03,
         -3.4238375e-03, -5.0024777e-03,  4.5454814e-03, -9.7530410e-03,
         -2.8278022e-03,  2.8969154e-03,  1.1389386e-03,  1.1044635e-03,
         -4.9849963e-03, -8.6261379e-04,  3.9018488e-03, -1.2971276e-03,
          4.7844523e-03]], dtype=float32),
 None)

In [66]:
print("mean reward after training:", np.mean(learner_rewards_after_training))
expert.predict(new_obs,deterministic=True)

mean reward after training: 1008.8973256349564


(array([[-4.9704066e-03, -2.9512034e-03, -3.8709978e-03, -1.5201775e-03,
         -3.7438609e-03,  4.1609872e-03,  2.7136467e-03,  4.6425788e-03,
         -6.8412279e-04,  2.6093577e-03, -3.4552373e-03, -4.4772876e-03,
          5.4676719e-03,  9.6433796e-03, -1.7450592e-03,  4.1021314e-04,
         -4.9753762e-03,  6.6392496e-04, -9.2622321e-03, -2.6082529e-03,
         -5.8745621e-03, -6.6485684e-03,  9.4102155e-03, -7.9215532e-03,
         -2.0311750e-03, -4.1278689e-03, -1.2732111e-05, -2.9133167e-04,
         -1.1158218e-02,  4.9406518e-03, -1.4419546e-03, -1.3260334e-03,
         -3.4238375e-03, -5.0024777e-03,  4.5454814e-03, -9.7530410e-03,
         -2.8278022e-03,  2.8969154e-03,  1.1389386e-03,  1.1044635e-03,
         -4.9849963e-03, -8.6261379e-04,  3.9018488e-03, -1.2971276e-03,
          4.7844523e-03]], dtype=float32),
 None)

In [13]:


airl_trainer.train(20000)  # Train for 2_000_000 steps to match expert.
venv.seed(SEED)
learner_rewards_after_training, _ = evaluate_policy(
    expert, venv, 100, return_episode_rewards=True,
)

print("mean reward after training:", np.mean(learner_rewards_after_training))
print("mean reward before training:", np.mean(learner_rewards_before_training))

round:   0%|          | 0/312 [00:00<?, ?it/s]

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
-------------------------------------
| raw/                        |     |
|    gen/time/fps             | 627 |
|    gen/time/iterations      | 1   |
|    gen/time/time_elapsed    | 0   |
|    gen/time/total_timesteps | 64  |
-------------------------------------
--------------------------------------------------
| raw/                                |          |
|    disc/disc_acc                    | 0.5      |
|    disc/disc_acc_expert             | 1        |
|    disc/disc_acc_gen                | 0        |
|    disc/disc_entropy                | 1.29e-25 |
|    disc/disc_loss                   | 32       |
|    disc/disc_proportion_expert_pred | 1        |
|    disc/disc_proportion_expert_true | 0.5      |
|    disc/global_step                 | 1        |
|    disc/n_expert                    | 2.

round:   0%|          | 1/312 [00:01<07:02,  1.36s/it]

64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
---------------------------------------------------
| raw/                              |             |
|    gen/time/fps                   | 500         |
|    gen/time/iterations            | 1           |
|    gen/time/time_elapsed          | 0           |
|    gen/time/total_timesteps       | 128         |
|    gen/train/approx_kl            | 0.032982703 |
|    gen/train/clip_fraction        | 0.242       |
|    gen/train/clip_range           | 0.2         |
|    gen/train/entropy_loss         | -63.9       |
|    gen/train/explained_variance   | -0.0358     |
|    gen/train/learning_rate        | 0.0003      |
|    gen/train/loss                 | 2.78        |
|    gen/train/n_updates            | 10          |
|    gen/train/policy_gradient_loss | -0.0813     |


round:   1%|          | 2/312 [00:02<06:19,  1.22s/it]

...

round: 100%|█████████▉| 311/312 [06:03<00:01,  1.16s/it]

404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
------------------------------------------------------
| raw/                               |               |
|    gen/rollout/ep_rew_wrapped_mean | -2.93e+04     |
|    gen/time/fps                    | 571           |
|    gen/time/iterations             | 1             |
|    gen/time/time_elapsed           | 0             |
|    gen/time/total_timesteps        | 19968         |
|    gen/train/approx_kl             | 0.00014270283 |
|    gen/train/clip_fraction         | 0             |
|    gen/train/clip_range            | 0.2           |
|    gen/train/entropy_loss          | -63.8         |
|    gen/train/explained_variance    | 3.4e-06       |
|    gen/train/learning_rate         | 0.0003        |
|    gen/train/loss          

round: 100%|██████████| 312/312 [06:04<00:00,  1.17s/it]

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211


212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
353
354
355
356
357
358
359
360
361
362
363
364
365
366
367
368
369
370
371
372
373
374
375
376
377
378
379
380
381
382
383
384
385
386
387
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461


In [96]:
expert = PPO(
    policy=MlpPolicy,
    env=env,
    seed=0,
    batch_size=64,
    ent_coef=0.0,
    learning_rate=0.0003,
    n_epochs=10,
    n_steps=64,
)

In [97]:
expert.learn(10_000)  # Note: set to 100000 to train a proficient expert
reward, _ = evaluate_policy(expert, expert.get_env(), 10)
print(f"Expert reward: {reward}")

Expert reward: -29.392361800000003


In [98]:
new_obs = np.random.randn(1,S.shape[1])
new_obs = torch.from_numpy(new_obs)

In [99]:

expert.predict(new_obs,deterministic=True)

(array([[ 1.0772369 ,  0.01825872,  0.64894027,  0.58522105, -0.42175424,
         -0.0744864 ,  0.14746852,  0.7274662 ,  1.8902161 , -0.18071777,
          0.3152242 ,  1.4564483 ,  0.49010503, -0.15784246,  0.52367914,
          0.13262574,  0.31092542,  0.25939438, -0.35044473, -0.14478081,
         -0.05530488, -0.5028756 ,  0.06508726,  0.9460253 ,  0.61002326,
          0.48299354,  0.3222123 , -0.7623597 ,  0.10786651, -0.2504192 ,
          0.9030931 , -0.62312734, -0.14495   ,  0.3723568 ,  0.8143641 ,
         -0.40870833,  1.4021727 , -0.0446986 ,  0.33985513, -0.13104138,
          0.58724755,  0.2506604 ,  0.4614539 ,  0.5921226 ,  0.77477515]],
       dtype=float32),
 None)

In [28]:
from imitation.algorithms import bc

bc_trainer = bc.BC(
    observation_space=venv.observation_space,
    action_space=venv.action_space,
    demonstrations=transitions,
    rng=rng,
)


In [102]:

reward_before_training, _ = evaluate_policy(bc_trainer.policy, venv, 10)
print(f"Reward before training: {reward_before_training}")


c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\stable_baselines3\common\evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Reward before training: -130.99549857902167


In [103]:

print(new_obs.shape[1])
action_2, _ = bc_trainer.policy.predict(new_obs,deterministic=True)
action_2

9


array([[ 0.00076871,  0.00375745,  0.0092989 ,  0.00170807, -0.00792869,
        -0.00272747,  0.00378536,  0.00590349,  0.00333346, -0.00317236,
         0.00710641, -0.00662428,  0.0079719 , -0.00533067,  0.00217031,
        -0.00563725,  0.00238183,  0.00154523,  0.00845461, -0.01066535,
         0.00336495,  0.0025418 ,  0.00346267, -0.00095958, -0.00563454,
         0.00018302, -0.00557083,  0.00129182, -0.0045753 , -0.0059214 ,
        -0.00212922,  0.00302794,  0.0011536 , -0.00111119, -0.00436008,
        -0.00506834, -0.00177586, -0.00122247, -0.00036921, -0.00105012,
         0.00573558,  0.00280472, -0.01016594,  0.00892089, -0.0013202 ]],
      dtype=float32)

In [30]:
print(f"Reward after training: {reward_after_training}")
print(new_obs.shape[1])
action_3, _ = bc_trainer.policy.predict(new_obs,deterministic=True)
action_3

Reward after training: 1007.863956451416
9


array([[ 0.00095535, -0.01815189,  0.03406592,  0.00647231,  0.00695273,
         0.0347929 ,  0.05767846, -0.00980637, -0.00527047, -0.01985778,
        -0.03400682,  0.00625889,  0.01560773, -0.00356263, -0.02455655,
         0.0124554 , -0.04491098, -0.0197854 , -0.03561569, -0.02933278,
         0.04940331,  0.02469139, -0.03299492,  0.00622646,  0.02870806,
        -0.0107629 ,  0.01431556, -0.0168446 ,  0.00849153,  0.01926448,
        -0.00254475, -0.00627102,  0.02622765,  0.00988088,  0.00657616,
         0.03393355,  0.02274074,  0.00566935, -0.01814046,  0.0644609 ,
        -0.00963278, -0.01609341, -0.00317729, -0.01323996,  0.00588682]],
      dtype=float32)

In [29]:
bc_trainer.train(n_epochs=10)
reward_after_training, _ = evaluate_policy(bc_trainer.policy, venv, 10)
print(f"Reward after training: {reward_after_training}")


0batch [00:00, ?batch/s]

--------------------------------
| batch_size        | 32       |
| bc/               |          |
|    batch          | 0        |
|    ent_loss       | -0.0639  |
|    entropy        | 63.9     |
|    epoch          | 0        |
|    l2_loss        | 0        |
|    l2_norm        | 82.5     |
|    loss           | 64.7     |
|    neglogp        | 64.8     |
|    prob_true_act  | 5.62e-27 |
|    samples_so_far | 32       |
--------------------------------


493batch [00:01, 247.44batch/s]

--------------------------------
| batch_size        | 32       |
| bc/               |          |
|    batch          | 500      |
|    ent_loss       | -0.0639  |
|    entropy        | 63.9     |
|    epoch          | 0        |
|    l2_loss        | 0        |
|    l2_norm        | 77.3     |
|    loss           | 63.6     |
|    neglogp        | 63.7     |
|    prob_true_act  | 3.08e-26 |
|    samples_so_far | 16032    |
--------------------------------


979batch [00:03, 259.63batch/s]

...

--------------------------------
| batch_size        | 32       |
| bc/               |          |
|    batch          | 7000     |
|    ent_loss       | -0.0638  |
|    entropy        | 63.8     |
|    epoch          | 8        |
|    l2_loss        | 0        |
|    l2_norm        | 68.7     |
|    loss           | 65.6     |
|    neglogp        | 65.6     |
|    prob_true_act  | 6.89e-27 |
|    samples_so_far | 224032   |
--------------------------------


7482batch [00:28, 258.59batch/s]

--------------------------------
| batch_size        | 32       |
| bc/               |          |
|    batch          | 7500     |
|    ent_loss       | -0.0639  |
|    entropy        | 63.9     |
|    epoch          | 9        |
|    l2_loss        | 0        |
|    l2_norm        | 68.5     |
|    loss           | 65       |
|    neglogp        | 65.1     |
|    prob_true_act  | 5.34e-26 |
|    samples_so_far | 240032   |
--------------------------------


7810batch [00:30, 259.33batch/s]
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\stable_baselines3\common\evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(
c:\Users\foresight_User\anaconda3\envs\Python3.9.13\lib\site-packages\imitation\data\types.py:279: UserWarning: tried to wrap <class 'torch.Tensor'> as an observation
  warnings.warn(f"tried to wrap {type(obs)} as an observation")


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27